# Description

This notebook takes in the sim_cahce file from the benrules_v2 simulator that runs random simulations on a given number of satellites.  We will extract the satellite data from all the the run simulations and combine into a single pandas dataframe. \

First part of the notebook is dedicated to visualizing satellite position over time.

# Imports

In [1]:
# Data Processing Libraries
import numpy as np
import pandas as pd
# Randomization Libraries to Select Random Points in the simulation.
import random
# Libraries for file reading
import h5py
# Bokeh and plotting related imports
# Plotting Imports
import bokeh.io
bokeh.io.output_notebook()  # Set plot output to embed in notebook.
import bokeh.layouts
import bokeh.plotting
# Other imports for multi-plot figures.
from bokeh.io import output_file, show
from bokeh.layouts import column
from bokeh.plotting import figure
# Memory management libraries for Python
import gc
# Progress Bar Libraries
from tqdm import tqdm

Loading BokehJS ...

In [2]:
# Remove max columns and row limit on pandas
pd.options.display.max_columns = None
pd.options.display.max_rows = 50000

# Setup Plotting Functions

In [3]:
from bokeh.palettes import Turbo256 as palette
import itertools
from random import randint

def plot_2D_body_time_series(pos_x_list, pos_y_list, plot_width, plot_height, title):
    """
    Accepts lists for x and y dimensions whose elements are time series data and whose
    index represents the number of the body in the simulation.
    
    returns Bokeh figure to plot.
    """
    # Create Bokeh figure to add plots to
    f = bokeh.plotting.figure(
        title = title,
        plot_width = plot_width,
        plot_height = plot_height
    )

    # Generate line for each body.
    # Randomly select color from palette using randint
    for i in range(0,len(pos_x_list)):
        f.line(
            pos_x_list[i],
            pos_y_list[i],
            line_width = 1,
            color = palette[randint(0,255)],
            legend_label = str(i)
        )
    f.legend.location = 'top_left'
    return f

def two_dim_numpy_data_to_2D_pos_list(sat_pos_list):
    """
    Take in a list of satellite position data and split into X and Y position data lists for 
    each dimension.
    """
    pos_x_list = []
    pos_y_list = []
    # Take the 2D (X and Y) time series elements of the sat_pos_list and split into the 
    # Pos_x and Pos_y lists
    for satellite_pos in sat_pos_list:
        temp_x_time_series = satellite_pos[:,0]
        temp_y_time_series = satellite_pos[:,1]
        pos_x_list.append(temp_x_time_series)
        pos_y_list.append(temp_y_time_series)
    return pos_x_list, pos_y_list

def plot_data_conv_3D_np_pos_to_2D_pos_list(pos_np_array):
    """
    Accepts 3D position numpy array and extracts the time steps for each body from 
    the numpy array.  Adds those time series for each dimension to a list of 1D numpy arrays.
    """
    # List of bodies for each dimension whose elements are numpy arrays going back in time.  
    # Each element is a time series for that body and that body's dimension.
    pos_x_list = []
    pos_y_list = []
    # First index of the numpy array is the time step and second is the body number.  Will loop
    # over all bodies and slice out the time steps for each body.
    for current_body_index in range(0, pos_np_array.shape[1]):
        # Get slice of data to create time series of position values
        # Use .to_numpy() to convert to numpy array
        temp_x_time_series = pos_np_array[:, current_body_index, 0]
        temp_y_time_series = pos_np_array[:, current_body_index, 1]
        # Add time series to respective dimension.
        pos_x_list.append(temp_x_time_series)
        pos_y_list.append(temp_y_time_series)
    
    # TODO: Continue with this function to get the position data plotted.
    return pos_x_list, pos_y_list

# Read in HDF5 Files to Lists of Numpy Arrays

In [4]:
# Set folder to read hdf5 cache file from.
in_data_folder = "input_data/"
# Body index in the numpy arrays from the simulation that designates the satellite from 
# the planets
sat_index: int = 10
# Lists for storing the satellite data from each simulation in the cache.
acc_list = []
vel_list = []
pos_list = []
dis_list = []
mass_list = []

# Open the sim_cache, get the data groups, and extract datasets from it.
with h5py.File(in_data_folder + 'sim_cache.hdf5', 'r') as f:
    # Get all the groups and data_set keys
    group_keys = []
    for key in f.keys():
        group_keys.append(key)
    # Loop over all groups in the dataset and extract the numpy arrays
    for group_name in group_keys:
        group = f[group_name]
        # Grab the raw data from the file.
        temp_acc = group['acc'][()]
        temp_vel = group['vel'][()]
        temp_pos = group['pos'][()]
        temp_dis = group['dis'][()]
        temp_mass = group['mass'][()]
        # Extract the Satellite data only
        # Only grabbing X and Y dimensions
        temp_acc = temp_acc[:, sat_index, 0:2]
        temp_vel = temp_vel[:, sat_index, 0:2]
        temp_pos = temp_pos[:, sat_index, 0:2]
        temp_dis = temp_dis[:, sat_index, 0:2]
        temp_mass = temp_mass[sat_index, 0]
        
        acc_list.append(temp_acc)
        vel_list.append(temp_vel)
        pos_list.append(temp_pos)
        dis_list.append(temp_dis)
        mass_list.append(temp_mass)

In [5]:
pos_list[0]

array([[-1.4818584e+11,  2.0621414e+10],
       [-1.4801456e+11,  2.1097075e+10],
       [-1.4784120e+11,  2.1573775e+10],
       ...,
       [-1.4375628e+11, -5.0585321e+10],
       [-1.4398502e+11, -5.0143236e+10],
       [-1.4421125e+11, -4.9700274e+10]], dtype=float32)

In [6]:
pos_list[0][:,0].shape

(39999,)

In [7]:
mass_list

[3499.0, 2123.0, 3406.0, 2699.0, 2723.0, 2375.0, 997.0, 1122.0, 2742.0, 3519.0]

# Plot the path of the Specified Satellite

In [8]:
# Convert all the satellite data to a list of time series for plotting.
# Will plot all satellites on the same plot.
pos_x_list, pos_y_list = two_dim_numpy_data_to_2D_pos_list(pos_list)

In [9]:
# Plot the converted data.
fig = plot_2D_body_time_series(
    pos_x_list = pos_x_list,
    pos_y_list = pos_y_list,
    plot_width = 800,
    plot_height = 800,
    title = "Paths of All Satellites for All Simulations"
)

bokeh.plotting.show(fig)

# Plot the Whole Universe with its Associated Satellite

Get the position data for the specified satellite and its universe and plot it.

In [10]:
# Set folder to read hdf5 cache file from.
in_data_folder = "input_data/"
# Index for the simulation to grab
sim_index: int = 0
# Lists for storing the satellite data from each simulation in the cache.
raw_pos_np = None

# Open the sim_cache, get the data groups, and extract datasets from it.
with h5py.File(in_data_folder + 'sim_cache.hdf5', 'r') as f:
    # Get data group for the specified index
    group_key = 'sim_' + str(sim_index)
    # Grab the position data for all bodies in that group.
    group = f[group_key]
    # Grab the raw data from the file.
    raw_pos_np = group['pos'][()]
# Convert to list of time series for plotting.  
pos_x_list, pos_y_list = plot_data_conv_3D_np_pos_to_2D_pos_list(raw_pos_np)
del raw_pos_np
# Plot the converted data.
fig = plot_2D_body_time_series(
    pos_x_list = pos_x_list,
    pos_y_list = pos_y_list,
    plot_width = 800,
    plot_height = 800,
    title = "Path of sat {} with Universe".format(sim_index)
)

bokeh.plotting.show(fig)

# Convert Acceleration, Velocity, Displacement, and Position Numpy Arrays to Pandas Dataframes

In [11]:
# Set the number of "shotgun" future time steps to predict.
num_ts_to_predict = 20

### Converting Acceleration to Pandas DataFrame

In [12]:
acc_list[0]

array([[0.00134939, 0.01014909],
       [0.00462917, 0.00191629],
       [0.00530746, 0.00037385],
       ...,
       [0.0053917 , 0.00189809],
       [0.00539286, 0.00187893],
       [0.00539403, 0.00185982]], dtype=float32)

In [13]:
# Stack all the satellites as bodies into a single numpy array.
stacked_raw_acc = np.stack(acc_list, axis=1)
stacked_raw_acc.shape

(39999, 10, 2)

In [14]:
# Construct the acceleration dataframe from the raw simulator velocity output data.
# Get the size of each dimension in numpy array.
# m-> the number of time steps in the simulation.
# n-> the number of bodies in the simulation.
# r-> number of dimensions in the vector holding the acceleration, displacement, etc.
acc_m,acc_n,acc_r = stacked_raw_acc.shape
# Stack the XY or XYZ arrays of each body into columns, removing a dimension.
# np.column_stack() -> takes a sequence of 1D arrays and stacks them as columns in a 2D matrix.
# np.arange() provides evenly spaced values that repeat n times.  The new index.
# Had to add 1 to arange to go from 1 to 79 instead of 0.
acc_arr = np.column_stack(
    (np.repeat(np.arange(1, acc_m+1, 1),acc_n), 
     np.tile(np.arange(0,acc_n,1),acc_m), 
     stacked_raw_acc[:,:,0:2].reshape(acc_m*acc_n,-1))
)

# Create dataframe from stacked column array.
acc_df = pd.DataFrame(acc_arr)
# Delete intermediate numpy arrays and original data from memory.
del acc_arr
gc.collect()
# Use df.groupby() to group by time step or planent and create MultiIndex for easy data referencing.
acc_df = acc_df.groupby([0,1]).mean()
acc_df.index.names = ['time_step', 'body']
acc_df.columns = ['acc_x', 'acc_y']
# Swapping to time_step then body to keep compatibility with existing code.
#acc_df = acc_df.swaplevel('time_step', 'body').sort_index(level=0)
#acc_df.head(15)
idx = pd.IndexSlice
acc_df.loc[idx[1, :], :]

acc_x     acc_y
time_step body                    
1.0       0.0   0.001349  0.010149
          1.0   0.004189  0.006091
          2.0  -0.006513  0.014888
          3.0   0.002247  0.007945
          4.0   0.005185  0.004996
          5.0  -0.015918  0.018924
          6.0   0.001365  0.010450
          7.0   0.004681  0.005216
          8.0   0.004218  0.006907
          9.0   0.004472  0.005535

In [15]:
# Drop the time steps that could not be used for calculating displacecment.
# Create list of time steps to drop.
beg_drop_index = max(acc_df.index.levels[0]) - num_ts_to_predict + 1
end_drop_index = max(acc_df.index.levels[0]) + 1
drop_list = list(range(int(beg_drop_index), int(end_drop_index)))
# Drop the time steps from the displacement dataframe.
acc_df.drop(drop_list, level=0, inplace=True)
# Ouput the new dataframe
acc_df.head(10)

acc_x     acc_y
time_step body                    
1.0       0.0   0.001349  0.010149
          1.0   0.004189  0.006091
          2.0  -0.006513  0.014888
          3.0   0.002247  0.007945
          4.0   0.005185  0.004996
          5.0  -0.015918  0.018924
          6.0   0.001365  0.010450
          7.0   0.004681  0.005216
          8.0   0.004218  0.006907
          9.0   0.004472  0.005535

In [16]:
acc_df.shape

(399790, 2)

### Converting Velocity to Pandas DataFrame

Dataframes are really slow.  We will need to calculate the future velocities for num_ts_to_predict so that we can shotgun predict multiple time steps at the same time.  We want to do this with numpy arrays before converting to a pandas dataframe for easy grouping and indexing. \
Will first need to go through and calculate the future time steps to shotgun-predict.

In [17]:
vel_list[0]

array([[  7911.1274,  21946.662 ],
       [  7987.891 ,  22044.395 ],
       [  8096.8413,  22065.303 ],
       ...,
       [-10649.889 ,  20444.76  ],
       [-10533.414 ,  20485.545 ],
       [-10416.915 ,  20525.916 ]], dtype=float32)

In [18]:
# Stack all the satellites as bodies into a single numpy array.
stacked_raw_vel = np.stack(vel_list, axis=1)
stacked_raw_vel.shape

(39999, 10, 2)

In [19]:
# Create a numpy array with the same first 2 dimensions of the input data (time steps and num bodies)
# the number of columns will be the same as the number of time steps
# being predicted multiplied by the dimensions (2) (X and Y)
vel_pred_cache = np.full(
    (stacked_raw_vel.shape[0], stacked_raw_vel.shape[1], num_ts_to_predict*2),
    np.nan,
    dtype=np.float32
)
# Loop over all time steps in the numpy array.
# Grab groups of bodies from future time steps
for curr_time_step in tqdm(range(0, stacked_raw_vel.shape[0])):
    # Loop over the number of time steps in the future to be grabbing
    # velocities from.
    # Don't do last time steps for displacement dataframe.  Can only look so many
    # time steps into the future before running out of data.
    if curr_time_step < (stacked_raw_vel.shape[0] - num_ts_to_predict):
        for num_ts_in_future in range(1, num_ts_to_predict + 1):
            vel_pred_cache[int(curr_time_step), :, int(2*num_ts_in_future-2):int(2*num_ts_in_future)] = \
            stacked_raw_vel[int(curr_time_step + num_ts_in_future), :, 0:2]
            
# Concatenate the cached numpy array to the original velocity dataset
stacked_raw_vel = np.concatenate((stacked_raw_vel[:,:,0:2], vel_pred_cache), axis=2)
# Delete the cache.
del vel_pred_cache
gc.collect()
#Display first portion of the dataframe
pd.DataFrame(stacked_raw_vel[0])

100%|██████████| 39999/39999 [00:01<00:00, 25909.76it/s]


0             1            2             3            4  \
0  7911.127441  21946.662109  7987.891113  22044.394531  8096.841309   
1  7308.379395  18837.378906  7416.748535  18891.783203  7537.179199   
2  8475.702148  25022.068359  8463.042969  25172.134766  8538.208008   
3  8259.713867  20912.921875  8347.098633  20987.072266  8460.213867   
4  6205.196777  17345.933594  6324.127930  17388.806641  6448.121582   
5  8211.469727  26777.634766  8084.529785  26973.201172  8111.811035   
6  7811.406250  22008.746094  7888.159180  22109.701172  7997.013184   
7  7006.160156  17840.435547  7119.886719  17885.603516  7242.204102   
8  6943.186035  19350.748047  7051.520020  19413.794922  7171.767578   
9  7184.007324  18247.347656  7295.476562  18295.880859  7417.012695   

              5            6             7            8             9  \
0  22065.302734  8214.647461  22066.347656  8336.202148  22059.095703   
1  18897.777344  7660.952148  18891.333984  7786.175293  18879.666016   
2  25212.134766  8638.068359  25223.113281  8748.434570  25221.898438   
3  20999.808594  8580.283203  20996.701172  8703.292969  20986.957031   
4  17390.941406  6573.633301  17382.625000  6699.844238  17369.914062   
5  27030.785156  8184.744141  27051.341797  8277.667969  27056.181641   
6  22131.726562  8114.743652  22133.339844  8236.236328  22126.433594   
7  17888.488281  7366.936035  17880.517578  7492.736816  17867.976562   
8  19422.724609  7295.379395  19417.751953  7420.454102  19406.960938   
9  18299.894531  7541.353027  18292.470703  7666.925293  18280.244141   

            10            11           12            13           14  \
0  8459.729492  22047.441406  8584.447266  22033.058594  8709.965820   
1  7912.198242  18865.185547  8038.736816  18848.921875  8165.652344   
2  8864.290039  25214.220703  8983.402344  25202.591797  9104.620117   
3  8827.868164  20973.658203  8953.409180  20958.128906  9079.609375   
4  6826.460938  17354.816406  6953.359863  17338.205078  7080.475098   
5  8381.208984  27052.681641  8491.104492  27044.072266  8605.122070   
6  8359.707031  22115.011719  8484.377930  22100.796875  8609.845703   
7  7619.145020  17852.957031  7745.956543  17836.361328  7873.071289   
8  7546.330078  19393.056641  7672.718262  19377.191406  7799.469727   
9  7793.185547  18265.408203  7919.898926  18248.927734  8046.947266   

             15           16            17           18            19  \
0  22016.792969  8836.058594  21999.117188  8962.590820  21980.314453   
1  18831.398438  8292.862305  18812.894531  8420.321289  18793.582031   
2  25188.275391  9227.294922  25171.976562  9351.025391  25154.134766   
3  20941.044922  9206.298828  20922.765625  9333.375000  20903.517578   
4  17320.507812  7207.771973  17301.966797  7335.230469  17282.724609   
5  27032.027344  8721.973633  27017.472656  8840.868164  27000.984375   
6  22084.666016  8735.887695  22067.089844  8862.367188  22048.365234   
7  17818.634766  8000.431641  17800.029297  8128.007324  17780.691406   
8  19359.951172  7926.503418  19341.654297  8053.769043  19322.494141   
9  18231.263672  8174.263672  18212.681641  8301.810547  18193.339844   

            20            21           22            23           24  \
0  9089.476562  21960.568359  9216.659180  21939.982422  9344.097656   
1  8547.997070  18773.574219  8675.873047  18752.939453  8803.933594   
2  9475.561523  25135.017578  9600.724609  25114.808594  9726.391602   
3  9460.771484  20883.435547  9588.449219  20862.613281  9716.375977   
4  7462.839355  17262.871094  7590.588867  17242.464844  7718.476074   
5  8961.283203  26982.925781  9082.870117  26963.544922  9205.381836   
6  8989.198242  22028.677734  9116.322266  22008.142578  9243.698242   
7  8255.777344  17760.720703  8383.730469  17740.171875  8511.854492   
8  8181.237793  19302.597656  8308.887695  19282.039062  8436.707031   
9  8429.563477  18173.339844  8557.505859  18152.744141  8685.629883   

             25           

In [20]:
# Construct the velocity dataframe from the raw simulator velocity output data.
# Get the size of each dimension in numpy array.
# m-> the number of time steps in the simulation.
# n-> the number of bodies in the simulation.
# r-> number of dimensions in the vector holding the acceleration, displacement, etc.
vel_m,vel_n,vel_r = stacked_raw_vel.shape
# Stack the XY or XYZ arrays of each body into columns, removing a dimension.
# np.column_stack() -> takes a sequence of 1D arrays and stacks them as columns in a 2D matrix.
# np.arange() provides evenly spaced values that repeat n times.  The new index.
# Had to add 1 to arange to go from 1 to 79 instead of 0.
vel_arr = np.column_stack(
    (np.repeat(np.arange(1, vel_m+1, 1),vel_n), 
     np.tile(np.arange(0,vel_n,1),vel_m), 
    stacked_raw_vel.reshape(vel_m*vel_n,-1))
)
# Create dataframe from stacked column array.
vel_df = pd.DataFrame(vel_arr)
# Delete intermediate numpy arrays and original data from memory.
del vel_arr
gc.collect()
# Use df.groupby() to group by time step or planent and create MultiIndex for easy data referencing.
vel_df = vel_df.groupby([0,1]).mean()
vel_df.index.names = ['time_step', 'body']
# Drop the time steps that could not be used for getting future data.
# Create list of time steps to drop.
beg_drop_index = max(vel_df.index.levels[0]) - num_ts_to_predict + 1
end_drop_index = max(vel_df.index.levels[0]) + 1
drop_list = list(range(int(beg_drop_index), int(end_drop_index)))
vel_df.drop(drop_list, level=0, inplace=True)
# Create list of columns 
cols = ['vel_x', 'vel_y']
for i in range(1, num_ts_to_predict+1):
    cols.append('vel_x_' + str(i))
    cols.append('vel_y_' + str(i))
vel_df.columns = cols
# View final velocity dataframe with future time steps.
idx = pd.IndexSlice
vel_df.loc[idx[0:2,:], :]

vel_x         vel_y      vel_x_1       vel_y_1  \
time_step body                                                         
1.0       0.0   7911.127441  21946.662109  7987.891113  22044.394531   
          1.0   7308.379395  18837.378906  7416.748535  18891.783203   
          2.0   8475.702148  25022.068359  8463.042969  25172.134766   
          3.0   8259.713867  20912.921875  8347.098633  20987.072266   
          4.0   6205.196777  17345.933594  6324.127930  17388.806641   
          5.0   8211.469727  26777.634766  8084.529785  26973.201172   
          6.0   7811.406250  22008.746094  7888.159180  22109.701172   
          7.0   7006.160156  17840.435547  7119.886719  17885.603516   
          8.0   6943.186035  19350.748047  7051.520020  19413.794922   
          9.0   7184.007324  18247.347656  7295.476562  18295.880859   
2.0       0.0   7987.891113  22044.394531  8096.841309  22065.302734   
          1.0   7416.748535  18891.783203  7537.179199  18897.777344   
          2.0   8463.042969  25172.134766  8538.208008  25212.134766   
          3.0   8347.098633  20987.072266  8460.213867  20999.808594   
          4.0   6324.127930  17388.806641  6448.121582  17390.941406   
          5.0   8084.529785  26973.201172  8111.811035  27030.785156   
          6.0   7888.159180  22109.701172  7997.013184  22131.726562   
          7.0   7119.886719  17885.603516  7242.204102  17888.488281   
          8.0   7051.520020  19413.794922  7171.767578  19422.724609   
          9.0   7295.476562  18295.880859  7417.012695  18299.894531   

                    vel_x_2       vel_y_2      vel_x_3       vel_y_3  \
time_step body                                                         
1.0       0.0   8096.841309  22065.302734  8214.647461  22066.347656   
          1.0   7537.179199  18897.777344  7660.952148  18891.333984   
          2.0   8538.208008  25212.134766  8638.068359  25223.113281   
          3.0   8460.213867  20999.808594  8580.283203  20996.701172   
          4.0   6448.121582  17390.941406  6573.633301  17382.625000   
          5.0   8111.811035  27030.785156  8184.744141  27051.341797   
          6.0   7997.013184  22131.726562  8114.743652  22133.339844   
          7.0   7242.204102  17888.488281  7366.936035  17880.517578   
          8.0   7171.767578  19422.724609  7295.379395  19417.751953   
          9.0   7417.012695  18299.894531  7541.353027  18292.470703   
2.0       0.0   8214.647461  22066.347656  8336.202148  22059.095703   
          1.0   7660.952148  18891.333984  7786.175293  18879.666016   
          2.0   8638.068359  25223.113281  8748.434570  25221.898438   
          3.0   8580.283203  20996.701172  8703.292969  20986.957031   
          4.0   6573.633301  17382.625000  6699.844238  17369.914062   
          5.0   8184.744141  27051.341797  8277.667969  27056.181641   
          6.0   8114.743652  22133.339844  8236.236328  22126.433594   
          7.0   7366.936035  17880.517578  7492.736816  17867.976562   
          8.0   7295.379395  19417.751953  7420.454102  19406.960938   
          9.0   7541.353027  18292.470703  7666.925293  18280.244141   

                    vel_x_4       vel_y_4      vel_x_5       vel_y_5  \
time_step body                                                         
1.0       0.0   8336.202148  22059.095703  8459.729492  22047.441406   
          1.0   7786.175293  18879.666016  7912.198242  18865.185547   
          2.0   8748.434570  25221.898438  8864.290039  25214.220703   
          3.0   8703.292969  20986.957031  8827.868164  20973.658203   
          4.0   6699.844238  17369.914062  6826.460938  17354.816406   
          5.0   8277.667969  27056.181641  8381.208984  27052.681641   
          6.0   8236.236328  22126.433594  8359.707031  22115.011719   
          7.0   7492.736816  17867.976562  7619.145020  17852.957031   
          8.0   7420.454102  19406.960938  7546.330078  19393.056641   
          9.0   7666.925293  18280.244141  7793.185547  1826

In [21]:
vel_df.shape

(399790, 42)

### Converting Displacement to Pandas DataFrame

In [22]:
# Stack all the satellites as bodies into a single numpy array.
stacked_raw_dis = np.stack(dis_list, axis=1)
stacked_raw_dis.shape

(39999, 10, 2)

In [23]:
# Create a numpy array with the same first 2 dimensions of the input data (time steps and num bodies)
# the number of columns will be the same as the number of time steps
# being predicted multiplied by the dimensions (2) (X and Y)
dis_pred_cache = np.full(
    (stacked_raw_dis.shape[0], stacked_raw_dis.shape[1], num_ts_to_predict*2),
    np.nan,
    dtype=np.float32
)
# Loop over all time steps in the numpy array.
# Grab groups of bodies from future time steps
for curr_time_step in tqdm(range(0, stacked_raw_dis.shape[0])):
    # Loop over the number of time steps in the future to be grabbing
    # velocities from.
    # Don't do last time steps for displacement dataframe.  Can only look so many
    # time steps into the future before running out of data.
    if curr_time_step < (stacked_raw_dis.shape[0] - num_ts_to_predict):
        for num_ts_in_future in range(1, num_ts_to_predict + 1):
            dis_pred_cache[int(curr_time_step), :, int(2*num_ts_in_future-2):int(2*num_ts_in_future)] = \
            stacked_raw_dis[int(curr_time_step + num_ts_in_future), :, 0:2]
            
# Concatenate the cached numpy array to the original displacement dataset
stacked_raw_dis = np.concatenate((stacked_raw_dis[:,:,0:2], dis_pred_cache), axis=2)
# Delete the cache.
del dis_pred_cache
gc.collect()
#Display first portion of the dataframe
pd.DataFrame(stacked_raw_dis[0])

100%|██████████| 39999/39999 [00:01<00:00, 30933.73it/s]


0           1          2           3          4           5  \
0  5696012.0  15801597.0  5751281.5  15871964.0  5829725.5  15887018.0   
1  5262033.0  13562913.0  5340059.0  13602084.0  5426769.0  13606400.0   
2  6102505.5  18015890.0  6093391.0  18123938.0  6147510.0  18152738.0   
3  5946994.0  15057304.0  6009911.0  15110692.0  6091354.0  15119862.0   
4  4467741.5  12489072.0  4553372.0  12519941.0  4642647.5  12521478.0   
5  5912258.0  19279898.0  5820861.5  19420704.0  5840504.0  19462166.0   
6  5624212.5  15846297.0  5679474.5  15918985.0  5757849.5  15934843.0   
7  5044435.5  12845114.0  5126318.5  12877635.0  5214387.0  12879712.0   
8  4999094.0  13932539.0  5077094.5  13977932.0  5163672.5  13984362.0   
9  5172485.5  13138090.0  5252743.0  13173034.0  5340249.0  13175924.0   

           6           7          8           9         10          11  \
0  5914546.0  15887770.0  6002065.5  15882549.0  6091005.0  15874158.0   
1  5515885.5  13601760.0  5606046.0  13593360.0  5696782.5  13582934.0   
2  6219409.0  18160642.0  6298873.0  18159766.0  6382289.0  18154238.0   
3  6177804.0  15117625.0  6266371.0  15110609.0  6356065.0  15101034.0   
4  4733016.0  12515490.0  4823888.0  12506338.0  4915052.0  12495468.0   
5  5893016.0  19476966.0  5959921.0  19480450.0  6034470.5  19477930.0   
6  5842615.5  15936005.0  5930090.0  15931032.0  6018989.0  15922808.0   
7  5304194.0  12873973.0  5394770.5  12864943.0  5485784.5  12854129.0   
8  5252673.0  13980781.0  5342727.0  13973012.0  5433357.5  13963001.0   
9  5429774.0  13170579.0  5520186.0  13161776.0  5611093.5  13151094.0   

          12          13         14          15         16          17  \
0  6180802.0  15863802.0  6271175.5  15852091.0  6361962.0  15839364.0   
1  5787890.5  13571224.0  5879269.5  13558607.0  5970861.0  13545284.0   
2  6468049.5  18145866.0  6555326.5  18135558.0  6643652.5  18123824.0   
3  6446454.5  15089853.0  6537319.0  15077552.0  6628535.0  15064391.0   
4  5006419.0  12483508.0  5097942.0  12470766.0  5189596.0  12457416.0   
5  6113595.0  19471732.0  6195688.0  19463060.0  6279821.0  19452580.0   
6  6108752.0  15912574.0  6199089.0  15900960.0  6289839.0  15888305.0   
7  5577088.5  12842180.0  5668611.5  12829417.0  5760311.0  12816021.0   
8  5524357.0  13951578.0  5615618.0  13939165.0  5707082.5  13925991.0   
9  5702327.0  13139228.0  5793802.0  13126510.0  5885470.0  13113131.0   

          18          19         20          21         22          23  \
0  6453065.5  15825826.0  6544423.0  15811609.0  6635994.5  15796787.0   
1  6062631.5  13531379.0  6154558.0  13516973.0  6246628.5  13502116.0   
2  6732738.5  18110978.0  6822404.5  18097212.0  6912521.5  18082662.0   
3  6720030.0  15050533.0  6811755.5  15036074.0  6903683.5  15021082.0   
4  5281366.0  12443562.0  5373244.5  12429267.0  5465224.0  12414575.0   
5  6365425.0  19440708.0  6452124.0  19427706.0  6539666.5  19413752.0   
6  6380904.5  15874823.0  6472222.5  15860648.0  6563752.0  15845863.0   
7  5852165.5  12802098.0  5944159.5  12787719.0  6036286.0  12772924.0   
8  5798713.5  13912196.0  5890491.0  13897870.0  5982399.0  13883068.0   
9  5977303.5  13099205.0  6069285.5  13084805.0  6161404.0  13069976.0   

          24          25         26          27         28          29  \
0  6727750.5  15781425.0  6819670.5  15765566.0  6911738.5  15749236.0   
1  6338832.0  13486843.0  6431164.5  13471180.0  6523619.0  13455145.0   
2  7003002.0  18067418.0  7093786.5  18051544.0  7184826.0  18035090.0   
3  6995790.5  15005606.0  7088060.5  14989674.0  7180485.0  14973313.0   
4  5557303.0  12399515.0  5649478.0  12384108.0  5741749.5  12368370.0   
5  6627875.0  19398970.0  6716616.5  19383450.0  6805793.0  19367254.0   
6  6655462.5  15830535.0  6747335.0  15814702.0  6839353.0  15798398.0   
7  6128535.0  12757742.0  6220905.0  12742199.0  6313392.5  12726307.0   
8  6074429.0  13867831.0  6166573.5  13852190.0  6258827.0  13836161.0   
9  6253653.

In [24]:
# Construct the displacement dataframe from the raw simulator displacement output data.
# Get the size of each dimension in numpy array.
# m-> the number of time steps in the simulation.
# n-> the number of bodies in the simulation.
# r-> number of dimensions in the vector holding the acceleration, displacement, etc.
dis_m,dis_n,dis_r = stacked_raw_dis.shape
# Stack the XY or XYZ arrays of each body into columns, removing a dimension.
# np.column_stack() -> takes a sequence of 1D arrays and stacks them as columns in a 2D matrix.
# np.arange() provides evenly spaced values that repeat n times.  The new index.
# Had to add 1 to arange to go from 1 to 79 instead of 0.
dis_arr = np.column_stack(
    (np.repeat(np.arange(1, dis_m+1, 1),dis_n), 
     np.tile(np.arange(0,dis_n,1),dis_m), 
     stacked_raw_dis.reshape(dis_m*dis_n,-1))
)
# Create dataframe from stacked column array.
dis_df = pd.DataFrame(dis_arr)
# Delete intermediate numpy arrays and original data from memory.
del dis_arr
gc.collect()
# Use df.groupby() to group by time step or planent and create MultiIndex for easy data referencing.
dis_df = dis_df.groupby([0,1]).mean()
dis_df.index.names = ['time_step', 'body']
# Drop the time steps that could not be used for getting future data.
# Create list of time steps to drop.
beg_drop_index = max(dis_df.index.levels[0]) - num_ts_to_predict + 1
end_drop_index = max(dis_df.index.levels[0]) + 1
drop_list = list(range(int(beg_drop_index), int(end_drop_index)))
dis_df.drop(drop_list, level=0, inplace=True)
# Create list of columns 
cols = ['dis_x', 'dis_y']
for i in range(1, num_ts_to_predict+1):
    cols.append('dis_x_' + str(i))
    cols.append('dis_y_' + str(i))
dis_df.columns = cols
# Drop dis_x and dis_y columns since we won't need then for ML training input.
dis_df.drop(['dis_x', 'dis_y'], axis=1,inplace=True)
# View final velocity dataframe with future time steps.
idx = pd.IndexSlice
dis_df.loc[idx[0:2,:], :]

dis_x_1     dis_y_1    dis_x_2     dis_y_2    dis_x_3  \
time_step body                                                            
1.0       0.0   5751281.5  15871964.0  5829725.5  15887018.0  5914546.0   
          1.0   5340059.0  13602084.0  5426769.0  13606400.0  5515885.5   
          2.0   6093391.0  18123938.0  6147510.0  18152738.0  6219409.0   
          3.0   6009911.0  15110692.0  6091354.0  15119862.0  6177804.0   
          4.0   4553372.0  12519941.0  4642647.5  12521478.0  4733016.0   
          5.0   5820861.5  19420704.0  5840504.0  19462166.0  5893016.0   
          6.0   5679474.5  15918985.0  5757849.5  15934843.0  5842615.5   
          7.0   5126318.5  12877635.0  5214387.0  12879712.0  5304194.0   
          8.0   5077094.5  13977932.0  5163672.5  13984362.0  5252673.0   
          9.0   5252743.0  13173034.0  5340249.0  13175924.0  5429774.0   
2.0       0.0   5829725.5  15887018.0  5914546.0  15887770.0  6002065.5   
          1.0   5426769.0  13606400.0  5515885.5  13601760.0  5606046.0   
          2.0   6147510.0  18152738.0  6219409.0  18160642.0  6298873.0   
          3.0   6091354.0  15119862.0  6177804.0  15117625.0  6266371.0   
          4.0   4642647.5  12521478.0  4733016.0  12515490.0  4823888.0   
          5.0   5840504.0  19462166.0  5893016.0  19476966.0  5959921.0   
          6.0   5757849.5  15934843.0  5842615.5  15936005.0  5930090.0   
          7.0   5214387.0  12879712.0  5304194.0  12873973.0  5394770.5   
          8.0   5163672.5  13984362.0  5252673.0  13980781.0  5342727.0   
          9.0   5340249.0  13175924.0  5429774.0  13170579.0  5520186.0   

                   dis_y_3    dis_x_4     dis_y_4    dis_x_5     dis_y_5  \
time_step body                                                             
1.0       0.0   15887770.0  6002065.5  15882549.0  6091005.0  15874158.0   
          1.0   13601760.0  5606046.0  13593360.0  5696782.5  13582934.0   
          2.0   18160642.0  6298873.0  18159766.0  6382289.0  18154238.0   
          3.0   15117625.0  6266371.0  15110609.0  6356065.0  15101034.0   
          4.0   12515490.0  4823888.0  12506338.0  4915052.0  12495468.0   
          5.0   19476966.0  5959921.0  19480450.0  6034470.5  19477930.0   
          6.0   15936005.0  5930090.0  15931032.0  6018989.0  15922808.0   
          7.0   12873973.0  5394770.5  12864943.0  5485784.5  12854129.0   
          8.0   13980781.0  5342727.0  13973012.0  5433357.5  13963001.0   
          9.0   13170579.0  5520186.0  13161776.0  5611093.5  13151094.0   
2.0       0.0   15882549.0  6091005.0  15874158.0  6180802.0  15863802.0   
          1.0   13593360.0  5696782.5  13582934.0  5787890.5  13571224.0   
          2.0   18159766.0  6382289.0  18154238.0  6468049.5  18145866.0   
          3.0   15110609.0  6356065.0  15101034.0  6446454.5  15089853.0   
          4.0   12506338.0  4915052.0  12495468.0  5006419.0  12483508.0   
          5.0   19480450.0  6034470.5  19477930.0  6113595.0  19471732.0   
          6.0   15931032.0  6018989.0  15922808.0  6108752.0  15912574.0   
          7.0   12864943.0  5485784.5  12854129.0  5577088.5  12842180.0   
          8.0   13973012.0  5433357.5  13963001.0  5524357.0  13951578.0   
          9.0   13161776.0  5611093.5  13151094.0  5702327.0  13139228.0   

                  dis_x_6     dis_y_6    dis_x_7     dis_y_7    dis_x_8  \
time_step body                                                            
1.0       0.0   6180802.0  15863802.0  6271175.5  15852091.0  6361962.0   
          1.0   5787890.5  13571224.0  5879269.5  13558607.0  5970861.0   
          2.0   6468049.5  18145866.0  6555326.5  18135558.0  6643652.5   
          3.0   6446454.5  15089853.0  6537319.0  15077552.0  6628535.0   
          4.0   5006419.0  12483508.0  5097942.0  12470766.0  5189596.0   
          5.0   6113595.0  19471732.0  6195688.0  19463060.0  6279821.0   
          6.0   6108752.0  15912574.0  6199089.0  15900960.0  6289839.0   
          7.0   557

In [25]:
dis_df.shape

(399790, 40)

### Converting Mass to Pandas DataFrame

In [26]:
stacked_raw_mass = np.array(mass_list)
stacked_raw_mass

array([3499., 2123., 3406., 2699., 2723., 2375.,  997., 1122., 2742.,
       3519.], dtype=float32)

In [27]:
# Construct the mass dataframe from the raw simulator mass output data.
# Get the size of each dimension in numpy array.
# m-> the number of time steps in the simulation.
# n-> the number of bodies in the simulation.
# r-> number of dimensions in the vector holding the acceleration, displacement, etc.
mass_n = stacked_raw_mass.shape[0]
# Stack the Mass column with the indexing columns.  Mass column will be repeated by the number
# of time steps.
# np.column_stack() -> takes a sequence of 1D arrays and stacks them as columns in a 2D matrix.
# np.arange() provides evenly spaced values that repeat n times.  The new index.
# Using displacement dataframe dimensions to copy the masses enough.
mass_arr = np.column_stack(
     (np.repeat(np.arange(1, dis_m+1, 1),mass_n), 
     np.tile(np.arange(0,mass_n,1), dis_m),
     np.tile(stacked_raw_mass.reshape(mass_n,), dis_m))
)
# Create dataframe from stacked column array.
mass_df = pd.DataFrame(mass_arr)
# Delete intermediate numpy arrays and original data from memory.
del mass_arr
gc.collect()
# Use df.groupby() to group by time step or planent and create MultiIndex for easy data referencing.
mass_df = mass_df.groupby([0,1]).mean()
mass_df.index.names = ['time_step', 'body']
mass_df.columns = ['mass']
# Drop the time steps that could not be used for getting future data.
# Create list of time steps to drop.
beg_drop_index = max(mass_df.index.levels[0]) - num_ts_to_predict + 1
end_drop_index = max(mass_df.index.levels[0]) + 1
drop_list = list(range(int(beg_drop_index), int(end_drop_index)))
mass_df.drop(drop_list, axis=0, inplace=True)
mass_df.head(15)

mass
time_step body        
1.0       0.0   3499.0
          1.0   2123.0
          2.0   3406.0
          3.0   2699.0
          4.0   2723.0
          5.0   2375.0
          6.0    997.0
          7.0   1122.0
          8.0   2742.0
          9.0   3519.0
2.0       0.0   3499.0
          1.0   2123.0
          2.0   3406.0
          3.0   2699.0
          4.0   2723.0

In [28]:
mass_df.shape

(399790, 1)

# Merge the Mass, Acceleration, Velocity, and Displacement Data

In [29]:
# Copy mass dataframe to start creating merged version.  Delete mass df afterwards.
merged_data = mass_df.copy(deep=True)
merged_data = pd.merge(merged_data, acc_df, left_index=True, right_index=True, how='outer')
# Delete mass_df and acc_df
del mass_df
del acc_df
gc.collect()
merged_data.head(15)

mass     acc_x     acc_y
time_step body                            
1.0       0.0   3499.0  0.001349  0.010149
          1.0   2123.0  0.004189  0.006091
          2.0   3406.0 -0.006513  0.014888
          3.0   2699.0  0.002247  0.007945
          4.0   2723.0  0.005185  0.004996
          5.0   2375.0 -0.015918  0.018924
          6.0    997.0  0.001365  0.010450
          7.0   1122.0  0.004681  0.005216
          8.0   2742.0  0.004218  0.006907
          9.0   3519.0  0.004472  0.005535
2.0       0.0   3499.0  0.004629  0.001916
          1.0   2123.0  0.005420  0.000872
          2.0   3406.0  0.002333  0.003227
          3.0   2699.0  0.004909  0.001345
          4.0   2723.0  0.005672  0.000598

In [30]:
# Merge in the velocity data.
merged_data = pd.merge(merged_data, vel_df, left_index=True, right_index=True, how='outer')
del vel_df
gc.collect()
merged_data.head(15)

mass     acc_x     acc_y        vel_x         vel_y  \
time_step body                                                          
1.0       0.0   3499.0  0.001349  0.010149  7911.127441  21946.662109   
          1.0   2123.0  0.004189  0.006091  7308.379395  18837.378906   
          2.0   3406.0 -0.006513  0.014888  8475.702148  25022.068359   
          3.0   2699.0  0.002247  0.007945  8259.713867  20912.921875   
          4.0   2723.0  0.005185  0.004996  6205.196777  17345.933594   
          5.0   2375.0 -0.015918  0.018924  8211.469727  26777.634766   
          6.0    997.0  0.001365  0.010450  7811.406250  22008.746094   
          7.0   1122.0  0.004681  0.005216  7006.160156  17840.435547   
          8.0   2742.0  0.004218  0.006907  6943.186035  19350.748047   
          9.0   3519.0  0.004472  0.005535  7184.007324  18247.347656   
2.0       0.0   3499.0  0.004629  0.001916  7987.891113  22044.394531   
          1.0   2123.0  0.005420  0.000872  7416.748535  18891.783203   
          2.0   3406.0  0.002333  0.003227  8463.042969  25172.134766   
          3.0   2699.0  0.004909  0.001345  8347.098633  20987.072266   
          4.0   2723.0  0.005672  0.000598  6324.127930  17388.806641   

                    vel_x_1       vel_y_1      vel_x_2       vel_y_2  \
time_step body                                                         
1.0       0.0   7987.891113  22044.394531  8096.841309  22065.302734   
          1.0   7416.748535  18891.783203  7537.179199  18897.777344   
          2.0   8463.042969  25172.134766  8538.208008  25212.134766   
          3.0   8347.098633  20987.072266  8460.213867  20999.808594   
          4.0   6324.127930  17388.806641  6448.121582  17390.941406   
          5.0   8084.529785  26973.201172  8111.811035  27030.785156   
          6.0   7888.159180  22109.701172  7997.013184  22131.726562   
          7.0   7119.886719  17885.603516  7242.204102  17888.488281   
          8.0   7051.520020  19413.794922  7171.767578  19422.724609   
          9.0   7295.476562  18295.880859  7417.012695  18299.894531   
2.0       0.0   8096.841309  22065.302734  8214.647461  22066.347656   
          1.0   7537.179199  18897.777344  7660.952148  18891.333984   
          2.0   8538.208008  25212.134766  8638.068359  25223.113281   
          3.0   8460.213867  20999.808594  8580.283203  20996.701172   
          4.0   6448.121582  17390.941406  6573.633301  17382.625000   

                    vel_x_3       vel_y_3      vel_x_4       vel_y_4  \
time_step body                                                         
1.0       0.0   8214.647461  22066.347656  8336.202148  22059.095703   
          1.0   7660.952148  18891.333984  7786.175293  18879.666016   
          2.0   8638.068359  25223.113281  8748.434570  25221.898438   
          3.0   8580.283203  20996.701172  8703.292969  20986.957031   
          4.0   6573.633301  17382.625000  6699.844238  17369.914062   
          5.0   8184.744141  27051.341797  8277.667969  27056.181641   
          6.0   8114.743652  22133.339844  8236.236328  22126.433594   
          7.0   7366.936035  17880.517578  7492.736816  17867.976562   
          8.0   7295.379395  19417.751953  7420.454102  19406.960938   
          9.0   7541.353027  18292.470703  7666.925293  18280.244141   
2.0       0.0   8336.202148  22059.095703  8459.729492  22047.441406   
          1.0   7786.175293  18879.666016  7912.198242  18865.185547   
          2.0   8748.434570  25221.898438  8864.290039  25214.220703   
          3.0   8703.292969  20986.957031  8827.868164  20973.658203   
          4.0   6699.844238  17369.914062  6826.460938  17354.816406   

                    vel_x_5       vel_y_5      vel_x_6       vel_y_6  \
time_step body                                                         
1.0       0.0   8459.729492  22047.441406  8584.447266  22033.058594   
          1.0   7912.198242  18865.185547  8038.736816  18848.921875   
          2.0   8864.290039  25214.220

In [31]:
# Merge in the displacement data
merged_data = pd.merge(merged_data, dis_df, left_index=True, right_index=True, how='outer')
del dis_df
gc.collect()
merged_data.head(15)

mass     acc_x     acc_y        vel_x         vel_y  \
time_step body                                                          
1.0       0.0   3499.0  0.001349  0.010149  7911.127441  21946.662109   
          1.0   2123.0  0.004189  0.006091  7308.379395  18837.378906   
          2.0   3406.0 -0.006513  0.014888  8475.702148  25022.068359   
          3.0   2699.0  0.002247  0.007945  8259.713867  20912.921875   
          4.0   2723.0  0.005185  0.004996  6205.196777  17345.933594   
          5.0   2375.0 -0.015918  0.018924  8211.469727  26777.634766   
          6.0    997.0  0.001365  0.010450  7811.406250  22008.746094   
          7.0   1122.0  0.004681  0.005216  7006.160156  17840.435547   
          8.0   2742.0  0.004218  0.006907  6943.186035  19350.748047   
          9.0   3519.0  0.004472  0.005535  7184.007324  18247.347656   
2.0       0.0   3499.0  0.004629  0.001916  7987.891113  22044.394531   
          1.0   2123.0  0.005420  0.000872  7416.748535  18891.783203   
          2.0   3406.0  0.002333  0.003227  8463.042969  25172.134766   
          3.0   2699.0  0.004909  0.001345  8347.098633  20987.072266   
          4.0   2723.0  0.005672  0.000598  6324.127930  17388.806641   

                    vel_x_1       vel_y_1      vel_x_2       vel_y_2  \
time_step body                                                         
1.0       0.0   7987.891113  22044.394531  8096.841309  22065.302734   
          1.0   7416.748535  18891.783203  7537.179199  18897.777344   
          2.0   8463.042969  25172.134766  8538.208008  25212.134766   
          3.0   8347.098633  20987.072266  8460.213867  20999.808594   
          4.0   6324.127930  17388.806641  6448.121582  17390.941406   
          5.0   8084.529785  26973.201172  8111.811035  27030.785156   
          6.0   7888.159180  22109.701172  7997.013184  22131.726562   
          7.0   7119.886719  17885.603516  7242.204102  17888.488281   
          8.0   7051.520020  19413.794922  7171.767578  19422.724609   
          9.0   7295.476562  18295.880859  7417.012695  18299.894531   
2.0       0.0   8096.841309  22065.302734  8214.647461  22066.347656   
          1.0   7537.179199  18897.777344  7660.952148  18891.333984   
          2.0   8538.208008  25212.134766  8638.068359  25223.113281   
          3.0   8460.213867  20999.808594  8580.283203  20996.701172   
          4.0   6448.121582  17390.941406  6573.633301  17382.625000   

                    vel_x_3       vel_y_3      vel_x_4       vel_y_4  \
time_step body                                                         
1.0       0.0   8214.647461  22066.347656  8336.202148  22059.095703   
          1.0   7660.952148  18891.333984  7786.175293  18879.666016   
          2.0   8638.068359  25223.113281  8748.434570  25221.898438   
          3.0   8580.283203  20996.701172  8703.292969  20986.957031   
          4.0   6573.633301  17382.625000  6699.844238  17369.914062   
          5.0   8184.744141  27051.341797  8277.667969  27056.181641   
          6.0   8114.743652  22133.339844  8236.236328  22126.433594   
          7.0   7366.936035  17880.517578  7492.736816  17867.976562   
          8.0   7295.379395  19417.751953  7420.454102  19406.960938   
          9.0   7541.353027  18292.470703  7666.925293  18280.244141   
2.0       0.0   8336.202148  22059.095703  8459.729492  22047.441406   
          1.0   7786.175293  18879.666016  7912.198242  18865.185547   
          2.0   8748.434570  25221.898438  8864.290039  25214.220703   
          3.0   8703.292969  20986.957031  8827.868164  20973.658203   
          4.0   6699.844238  17369.914062  6826.460938  17354.816406   

                    vel_x_5       vel_y_5      vel_x_6       vel_y_6  \
time_step body                                                         
1.0       0.0   8459.729492  22047.441406  8584.447266  22033.058594   
          1.0   7912.198242  18865.185547  8038.736816  18848.921875   
          2.0   8864.290039  25214.220

In [32]:
# Rearrange columns so they are in the needed order.
# Create list of what the column order should be.
cols = []
cols.extend(['mass', 'acc_x', 'acc_y', 'vel_x', 'vel_y'])
# Loop over all the time steps we wanted to predict and rearrange the columns
# accordingly
for i in range(1,num_ts_to_predict+1):
    cols.append('dis_x_' + str(i))
    cols.append('dis_y_' + str(i))
    cols.append('vel_x_' + str(i))
    cols.append('vel_y_' + str(i))
# Rearrange columns using the create columns list.
merged_data = merged_data[cols]
merged_data.head(15)

mass     acc_x     acc_y        vel_x         vel_y  \
time_step body                                                          
1.0       0.0   3499.0  0.001349  0.010149  7911.127441  21946.662109   
          1.0   2123.0  0.004189  0.006091  7308.379395  18837.378906   
          2.0   3406.0 -0.006513  0.014888  8475.702148  25022.068359   
          3.0   2699.0  0.002247  0.007945  8259.713867  20912.921875   
          4.0   2723.0  0.005185  0.004996  6205.196777  17345.933594   
          5.0   2375.0 -0.015918  0.018924  8211.469727  26777.634766   
          6.0    997.0  0.001365  0.010450  7811.406250  22008.746094   
          7.0   1122.0  0.004681  0.005216  7006.160156  17840.435547   
          8.0   2742.0  0.004218  0.006907  6943.186035  19350.748047   
          9.0   3519.0  0.004472  0.005535  7184.007324  18247.347656   
2.0       0.0   3499.0  0.004629  0.001916  7987.891113  22044.394531   
          1.0   2123.0  0.005420  0.000872  7416.748535  18891.783203   
          2.0   3406.0  0.002333  0.003227  8463.042969  25172.134766   
          3.0   2699.0  0.004909  0.001345  8347.098633  20987.072266   
          4.0   2723.0  0.005672  0.000598  6324.127930  17388.806641   

                  dis_x_1     dis_y_1      vel_x_1       vel_y_1    dis_x_2  \
time_step body                                                                
1.0       0.0   5751281.5  15871964.0  7987.891113  22044.394531  5829725.5   
          1.0   5340059.0  13602084.0  7416.748535  18891.783203  5426769.0   
          2.0   6093391.0  18123938.0  8463.042969  25172.134766  6147510.0   
          3.0   6009911.0  15110692.0  8347.098633  20987.072266  6091354.0   
          4.0   4553372.0  12519941.0  6324.127930  17388.806641  4642647.5   
          5.0   5820861.5  19420704.0  8084.529785  26973.201172  5840504.0   
          6.0   5679474.5  15918985.0  7888.159180  22109.701172  5757849.5   
          7.0   5126318.5  12877635.0  7119.886719  17885.603516  5214387.0   
          8.0   5077094.5  13977932.0  7051.520020  19413.794922  5163672.5   
          9.0   5252743.0  13173034.0  7295.476562  18295.880859  5340249.0   
2.0       0.0   5829725.5  15887018.0  8096.841309  22065.302734  5914546.0   
          1.0   5426769.0  13606400.0  7537.179199  18897.777344  5515885.5   
          2.0   6147510.0  18152738.0  8538.208008  25212.134766  6219409.0   
          3.0   6091354.0  15119862.0  8460.213867  20999.808594  6177804.0   
          4.0   4642647.5  12521478.0  6448.121582  17390.941406  4733016.0   

                   dis_y_2      vel_x_2       vel_y_2    dis_x_3     dis_y_3  \
time_step body                                                                 
1.0       0.0   15887018.0  8096.841309  22065.302734  5914546.0  15887770.0   
          1.0   13606400.0  7537.179199  18897.777344  5515885.5  13601760.0   
          2.0   18152738.0  8538.208008  25212.134766  6219409.0  18160642.0   
          3.0   15119862.0  8460.213867  20999.808594  6177804.0  15117625.0   
          4.0   12521478.0  6448.121582  17390.941406  4733016.0  12515490.0   
          5.0   19462166.0  8111.811035  27030.785156  5893016.0  19476966.0   
          6.0   15934843.0  7997.013184  22131.726562  5842615.5  15936005.0   
          7.0   12879712.0  7242.204102  17888.488281  5304194.0  12873973.0   
          8.0   13984362.0  7171.767578  19422.724609  5252673.0  13980781.0   
          9.0   13175924.0  7417.012695  18299.894531  5429774.0  13170579.0   
2.0       0.0   15887770.0  8214.647461  22066.347656  6002065.5  15882549.0   
          1.0   13601760.0  7660.952148  18891.333984  5606046.0  13593360.0   
          2.0   18160642.0  8638.068359  25223.113281  6298873.0  18159766.0   
          3.0   15117625.0  8580.283203  20996.701172  6266371.0  15110609.0   
          4.0   12515490.0  6573.633301  17382.625000  4823888.0  12506338.0   

                    vel_x_3       vel_y_3    dis_x_4     dis_y_4      v

# Create Body Time Series Data Format

In [33]:
merged_data_time_series = merged_data.copy(deep=True)
merged_data_time_series = merged_data_time_series.swaplevel('time_step', 'body').sort_index(level=0)
merged_data_time_series.head(15)

mass     acc_x     acc_y        vel_x         vel_y  \
body time_step                                                          
0.0  1.0        3499.0  0.001349  0.010149  7911.127441  21946.662109   
     2.0        3499.0  0.004629  0.001916  7987.891113  22044.394531   
     3.0        3499.0  0.005307  0.000374  8096.841309  22065.302734   
     4.0        3499.0  0.005558 -0.000182  8214.647461  22066.347656   
     5.0        3499.0  0.005680 -0.000452  8336.202148  22059.095703   
     6.0        3499.0  0.005750 -0.000609  8459.729492  22047.441406   
     7.0        3499.0  0.005794 -0.000713  8584.447266  22033.058594   
     8.0        3499.0  0.005825 -0.000787  8709.965820  22016.792969   
     9.0        3499.0  0.005848 -0.000845  8836.058594  21999.117188   
     10.0       3499.0  0.005866 -0.000893  8962.590820  21980.314453   
     11.0       3499.0  0.005881 -0.000934  9089.476562  21960.568359   
     12.0       3499.0  0.005894 -0.000970  9216.659180  21939.982422   
     13.0       3499.0  0.005905 -0.001004  9344.097656  21918.646484   
     14.0       3499.0  0.005915 -0.001035  9471.764648  21896.619141   
     15.0       3499.0  0.005924 -0.001064  9599.636719  21873.939453   

                  dis_x_1     dis_y_1      vel_x_1       vel_y_1    dis_x_2  \
body time_step                                                                
0.0  1.0        5751281.5  15871964.0  7987.891113  22044.394531  5829725.5   
     2.0        5829725.5  15887018.0  8096.841309  22065.302734  5914546.0   
     3.0        5914546.0  15887770.0  8214.647461  22066.347656  6002065.5   
     4.0        6002065.5  15882549.0  8336.202148  22059.095703  6091005.0   
     5.0        6091005.0  15874158.0  8459.729492  22047.441406  6180802.0   
     6.0        6180802.0  15863802.0  8584.447266  22033.058594  6271175.5   
     7.0        6271175.5  15852091.0  8709.965820  22016.792969  6361962.0   
     8.0        6361962.0  15839364.0  8836.058594  21999.117188  6453065.5   
     9.0        6453065.5  15825826.0  8962.590820  21980.314453  6544423.0   
     10.0       6544423.0  15811609.0  9089.476562  21960.568359  6635994.5   
     11.0       6635994.5  15796787.0  9216.659180  21939.982422  6727750.5   
     12.0       6727750.5  15781425.0  9344.097656  21918.646484  6819670.5   
     13.0       6819670.5  15765566.0  9471.764648  21896.619141  6911738.5   
     14.0       6911738.5  15749236.0  9599.636719  21873.939453  7003944.0   
     15.0       7003944.0  15732463.0  9727.700195  21850.642578  7096278.0   

                   dis_y_2      vel_x_2       vel_y_2    dis_x_3     dis_y_3  \
body time_step                                                                 
0.0  1.0        15887018.0  8096.841309  22065.302734  5914546.0  15887770.0   
     2.0        15887770.0  8214.647461  22066.347656  6002065.5  15882549.0   
     3.0        15882549.0  8336.202148  22059.095703  6091005.0  15874158.0   
     4.0        15874158.0  8459.729492  22047.441406  6180802.0  15863802.0   
     5.0        15863802.0  8584.447266  22033.058594  6271175.5  15852091.0   
     6.0        15852091.0  8709.965820  22016.792969  6361962.0  15839364.0   
     7.0        15839364.0  8836.058594  21999.117188  6453065.5  15825826.0   
     8.0        15825826.0  8962.590820  21980.314453  6544423.0  15811609.0   
     9.0        15811609.0  9089.476562  21960.568359  6635994.5  15796787.0   
     10.0       15796787.0  9216.659180  21939.982422  6727750.5  15781425.0   
     11.0       15781425.0  9344.097656  21918.646484  6819670.5  15765566.0   
     12.0       15765566.0  9471.764648  21896.619141  6911738.5  15749236.0   
     13.0       15749236.0  9599.636719  21873.939453  7003944.0  15732463.0   
     14.0       15732463.0  9727.700195  21850.642578  7096278.0  15715257.0   
     15.0       15715257.0  9855.941406  21826.746094  7188734.5  15697640.0   

                    vel_x_3       vel_y_3    dis_x_4     dis_y_4  \
bod

# Attempt Converting Merged Datasets to Numpy Arrays and Save as Both Pd dataframes and Np Arrays

In [34]:
merged_data.to_numpy().shape

(399790, 85)

In [35]:
dim0 = len(merged_data.index.get_level_values(0).unique())
dim1 = len(merged_data.index.get_level_values(1).unique())
dim2 = merged_data.shape[1]
merged_data_ndarray = merged_data.to_numpy().reshape((dim0, dim1, dim2))
merged_data_ndarray[0,0]

array([3.49900000e+03, 1.34938781e-03, 1.01490859e-02, 7.91112744e+03,
       2.19466621e+04, 5.75128150e+06, 1.58719640e+07, 7.98789111e+03,
       2.20443945e+04, 5.82972550e+06, 1.58870180e+07, 8.09684131e+03,
       2.20653027e+04, 5.91454600e+06, 1.58877700e+07, 8.21464746e+03,
       2.20663477e+04, 6.00206550e+06, 1.58825490e+07, 8.33620215e+03,
       2.20590957e+04, 6.09100500e+06, 1.58741580e+07, 8.45972949e+03,
       2.20474414e+04, 6.18080200e+06, 1.58638020e+07, 8.58444727e+03,
       2.20330586e+04, 6.27117550e+06, 1.58520910e+07, 8.70996582e+03,
       2.20167930e+04, 6.36196200e+06, 1.58393640e+07, 8.83605859e+03,
       2.19991172e+04, 6.45306550e+06, 1.58258260e+07, 8.96259082e+03,
       2.19803145e+04, 6.54442300e+06, 1.58116090e+07, 9.08947656e+03,
       2.19605684e+04, 6.63599450e+06, 1.57967870e+07, 9.21665918e+03,
       2.19399824e+04, 6.72775050e+06, 1.57814250e+07, 9.34409766e+03,
       2.19186465e+04, 6.81967050e+06, 1.57655660e+07, 9.47176465e+03,
      

In [36]:
dim0 = len(merged_data_time_series.index.get_level_values(0).unique())
dim1 = len(merged_data_time_series.index.get_level_values(1).unique())
dim2 = merged_data.shape[1]
merged_data_time_series_ndarray = merged_data_time_series.to_numpy().reshape((dim0, dim1, dim2))
merged_data_time_series_ndarray[0,5]

array([ 3.49900000e+03,  5.74963633e-03, -6.09266921e-04,  8.45972949e+03,
        2.20474414e+04,  6.18080200e+06,  1.58638020e+07,  8.58444727e+03,
        2.20330586e+04,  6.27117550e+06,  1.58520910e+07,  8.70996582e+03,
        2.20167930e+04,  6.36196200e+06,  1.58393640e+07,  8.83605859e+03,
        2.19991172e+04,  6.45306550e+06,  1.58258260e+07,  8.96259082e+03,
        2.19803145e+04,  6.54442300e+06,  1.58116090e+07,  9.08947656e+03,
        2.19605684e+04,  6.63599450e+06,  1.57967870e+07,  9.21665918e+03,
        2.19399824e+04,  6.72775050e+06,  1.57814250e+07,  9.34409766e+03,
        2.19186465e+04,  6.81967050e+06,  1.57655660e+07,  9.47176465e+03,
        2.18966191e+04,  6.91173850e+06,  1.57492360e+07,  9.59963672e+03,
        2.18739395e+04,  7.00394400e+06,  1.57324630e+07,  9.72770020e+03,
        2.18506426e+04,  7.09627800e+06,  1.57152570e+07,  9.85594141e+03,
        2.18267461e+04,  7.18873450e+06,  1.56976400e+07,  9.98435352e+03,
        2.18022773e+04,  

## Save the Numpy Arrays and Pandas Dataframes

In [37]:
# Set the output directory.
out_dir = 'output/'

Save the dataframes by pickling them.

In [38]:
# Save using 'default' as the key.
# https://pythontic.com/pandas/serialization/hdf5

#merged_data.to_hdf(out_dir + 'sim_data_df-ts-body.hdf5', 'default')

file_name = '3-hour_10-sats_predict-20-steps_720ts_1200000steps_30freq.hdf5'
merged_data_time_series.to_hdf(out_dir + file_name, 'default')

# merged_data.to_pickle(out_dir + 'sim_data_df-ts-body.pkl')
# merged_data_time_series.to_pickle(out_dir + 'sim_data_df-body-ts.pkl')

Save the dataframes to XLSX files to view in Excel. \
Some larger datasets can't be saved to Excel.  Takes forever to parse the file.

In [ ]:
# merged_data.to_excel(out_dir + 'sim_data_df-ts-body.xlsx')
# merged_data_time_series.to_excel(out_dir + 'sim_data_df-body-ts.xlsx')

Save the numpy arrays by using numpy's saving function.

In [ ]:
#np.save(out_dir + 'sim_data_np-ts-body.npy', merged_data_ndarray)
#np.save(out_dir + 'sim_data_np-body-ts.npy', merged_data_time_series_ndarray)